# To do

### comparaison between the 2-equations and 3-equations model
### write a Lie seperator and compare
### find the appropriate time step for splitting method

### compute error function is in the mod_utils.f90

* the error will appear only when neq=2, the error is computed for b and c


In [1]:
import numpy as np
import pandas as pd
from scipy.integrate import solve_ivp
from outil import write_input, read_data
import os
from bokeh.io import  output_notebook, push_notebook, show
from bokeh.plotting import figure
from bokeh.layouts import column, row
from bokeh.palettes import Category10,Category20
from bokeh.models import PrintfTickFormatter

from ipywidgets import FloatProgress, IntProgress
from IPython.display import display

output_notebook(hide_banner=True)

## Change input parameter

In [2]:
#type of model (nb of equations) : 2 or 3 
neq=3
#tini: intial time
tini=0.0
#tend: final time
tend=2
#nt: nb of time discretization points to compute splitting time step
nt=int(tend*100)+1
#xmin: left limit of domain
xmin=0.0
#xmax: right limit of domain
xmax=4.0
#nx: nb of spatial discretization points
nx=4001
#method: integration method (radau5, strang,lie_dr, lie_rd, strang_drd)
method='strang_drd'
#tol: tolerance for radau5 and rock4
tol='1.d-06'
list_input=[neq,tini,tend,nt,xmin,xmax,nx,method,tol]
write_input(list_input)

neq = 3	 
tini = 0.0	 
tend = 2	 
nt = 201	 
xmin = 0.0	 
xmax = 4.0	 
nx = 4001	 
method = strang_drd	 
tol = 1.d-06	 



## Resolution of the system

In [3]:
os.chdir('/home/te/Study/MAP551_Projet/bz_1d')
print(os.popen('make').read())
os.chdir('/home/te/Study/MAP551_Projet/bz_1d/run')

make: Nothing to be done for 'default'.



In [33]:
print(os.popen('./bz_1d').read())

 Resolution of BZ equation
 Model with 3 species
   neq   =           3
   tini =        0.000
   tend =        2.000
   nt   =         201
   xmin =       0.000
   xmax =       4.000
   nxib =        4001
   integration method : strang_drd          
   tolerance (for Radau5 and Rock4) =   1.000E-06

 Strang diffusion-reaction-diffusion splitting integration
   RADAU5 for reaction
   ROCK4  for diffusion
   Splitting time step = 0.1000E-01
   Iteration     1  t = 0.1000E-01
   Iteration     2  t = 0.2000E-01
   Iteration     3  t = 0.3000E-01
   Iteration     4  t = 0.4000E-01
   Iteration     5  t = 0.5000E-01
   Iteration     6  t = 0.6000E-01
   Iteration     7  t = 0.7000E-01
   Iteration     8  t = 0.8000E-01
   Iteration     9  t = 0.9000E-01
   Iteration    10  t = 0.1000E+00
   Iteration    11  t = 0.1100E+00
   Iteration    12  t = 0.1200E+00
   Iteration    13  t = 0.1300E+00
   Iteration    14  t = 0.1400E+00
   Iteration    15  t = 0.1500E+00
   Iteration    16  t = 0.1600E

In [34]:
#for two equations
if(neq==2):
    sol_init,num_init=read_data("sol_ini.dat")
    sol_final,num_final=read_data("sol_num.dat")
    #quasi exact solution with high tolerance
    sol_ref, num_ref=read_data("sol_ref2.dat")
    dx=sol_final[0,2]-sol_final[0,1]
    err_b=np.linalg.norm(sol_final[1]-sol_ref[1])*np.sqrt(dx)
    err_c=np.linalg.norm(sol_final[2]-sol_ref[2])*np.sqrt(dx)
    print('Variable b : || unum - uexa || = ' ,err_b)
    print('Variable c : || unum - uexa || = ' ,err_c)
#for three equations
else:
    sol_init,num_init=read_data("sol_ini.dat")
    sol_final,num_final=read_data("sol_num.dat")
    #quasi exact solution with high tolerance
    sol_ref, num_ref=read_data("sol_ref3.dat")
    dx=sol_final[0,2]-sol_final[0,1]
    err_a=np.linalg.norm(sol_final[1]-sol_ref[1])*np.sqrt(dx)
    err_b=np.linalg.norm(sol_final[2]-sol_ref[2])*np.sqrt(dx)
    err_c=np.linalg.norm(sol_final[3]-sol_ref[3])*np.sqrt(dx)
    print('Variable a : || unum - uexa || = ' ,err_a)
    print('Variable b : || unum - uexa || = ' ,err_b)
    print('Variable c : || unum - uexa || = ' ,err_c)
x=sol_final[0]

#  can not be converted in to a float
#  can not be converted in to a float
#  can not be converted in to a float
Variable a : || unum - uexa || =  30.255902636912385
Variable b : || unum - uexa || =  0.057067482890988966
Variable c : || unum - uexa || =  0.0032248337828479873


### Comparaison between the strang splitting and quasi exact Radeau5  ($tol=10^{-12}$)

In [35]:
if(neq==2):
    fig_solb = figure(x_range=(xmin,xmax), plot_height=400, plot_width=950, title="Solution")
    fig_solc = figure(x_range=(xmin,xmax), plot_height=400, plot_width=950, title="Solution")
    fig_solc.line(x, sol_init[2],line_width=3,color="Green",legend='solution initiale_c')
    fig_solc.x(x, sol_final[2],line_width=1,legend='solution num_c')
    fig_solc.line(x,sol_ref[2],color="crimson",legend='Quasi exact')
    
    fig_solb.line(x, sol_init[1],line_width=3,color="Green",legend='solution initiale_b')
    fig_solb.x(x, sol_final[1],line_width=1,legend='solution num_b')
    fig_solb.line(x,sol_ref[1],color="crimson",legend='Quasi exact')
    show(column(fig_solb,fig_solc))
if(neq==3):
    fig_sola = figure(x_range=(xmin,xmax), plot_height=400, plot_width=950, title="Solution a")
    fig_sola.line(x, sol_init[1],line_width=3,color="Green",legend='solution initiale a')
    fig_sola.x(x, sol_final[1],line_width=1,legend='solution num_a')
    fig_sola.line(x,sol_ref[1],color="crimson",legend='Quasi exact')
    
    fig_solb = figure(x_range=(xmin,xmax), plot_height=400, plot_width=950, title="Solution b")
    fig_solb.line(x, sol_init[2],line_width=3,color="Green",legend='solution initiale b')
    fig_solb.x(x, sol_final[2],line_width=1,legend='solution num_b')
    fig_solb.line(x,sol_ref[2],color="crimson",legend='Quasi exact')
    
    fig_solc = figure(x_range=(xmin,xmax), plot_height=400, plot_width=950, title="Solution c")
    fig_solc.line(x, sol_init[3],line_width=3,color="Green",legend='solution initiale c')
    fig_solc.x(x, sol_final[3],line_width=1,legend='solution num_c')
    fig_solc.line(x,sol_ref[3],color="crimson",legend='Quasi exact')
    show(column(fig_sola,fig_solb,fig_solc))

In [19]:
if(neq==3):
    fig_err=figure(x_range=(xmin,xmax), y_range=(-5.e-5,5.e-5),plot_height=400, plot_width=950)
    err=sol_final-sol_ref
    fig_err.x(x,err[1], color=Category10[10][1], legend='Err_a')
    fig_err.x(x,err[2], color=Category10[10][2], legend='Err_b')
    fig_err.x(x,err[3], color=Category10[10][3], legend='Err_c')
    show(fig_err)
else:
    fig_err=figure(x_range=(xmin,xmax),plot_height=400, plot_width=950)
    err=sol_final-sol_ref
    fig_err.x(x,err[1], color=Category10[10][1], legend='Err_b')
    fig_err.x(x,err[2], color=Category10[10][2], legend='Err_c')
    show(fig_err)    

# Question 2.1: 

### Simulate the propagation of the wave in  time. Show that there is a limit splitting time step for which the velocity of the wave is not predicted accurately any more

In [107]:
#type of model (nb of equations) : 2 or 3 
neq=3
#tini: intial time
tini=0.0
#xmin: left limit of domain
xmin=0.0
#xmax: right limit of domain
xmax=4.0
#nx: nb of spatial discretization points
nx=4001
#method: integration method (radau5, strang)
method='radau5'
#tol: tolerance for radau5 and rock4
tol='1.d-12'

tend_start, tend_final, num_plot=0.5,5.5, 11

In [108]:
# it takes hundurds of years to do, unlesse you do think it is necessary to exacute 
'''
sols=[]
for tend in np.linspace(tend_start,tend_final, num_plot):
    nt=int(tend*100)+1
    list_input=[neq,tini,tend,nt,xmin,xmax,nx,method,tol]
    write_input(list_input)
    os.system('./bz_1d')
    sol_final,num_final=read_data("sol_num.dat")
    sols.append(sol_final)
np.save('traveling_waves_neq'+str(neq)+'.npy',np.array(sols))
'''

'\nsols=[]\nfor tend in np.linspace(tend_start,tend_final, num_plot):\n    nt=int(tend*100)+1\n    list_input=[neq,tini,tend,nt,xmin,xmax,nx,method,tol]\n    write_input(list_input)\n    os.system(\'./bz_1d\')\n    sol_final,num_final=read_data("sol_num.dat")\n    sols.append(sol_final)\nnp.save(\'traveling_waves_neq\'+str(neq)+\'.npy\',np.array(sols))\n'

In [109]:
def velocity(sols,x,time_step):
    c=[[]]
    for j in range(1,len(sols[0])):
        index_after =sols[0][j].argmax()
        v=(x[index_after]-0)/time_step
        c[0].append(v)
        
    for i in range(1,len(sols)):
        c.append([])
        for j in range(1,len(sols[0])):
            index_before=sols[i-1][j].argmax()
            index_after =sols[i][j].argmax()
            v=(x[index_after]-x[index_before])/time_step
            c[i].append(v)
    return np.array(c).T
        

### The concentration of each chemical substance

In [110]:
# sicne the data is already here, we can run this cell directrly
sols=np.load('traveling_waves_neq'+str(neq)+'.npy')
sol_init,num_init=read_data("sol_ini.dat")
x=sol_init[0]
t_plot=[]
for tend in np.linspace(tend_start,tend_final, num_plot):t_plot.append(tend)
if(neq==2):
    fig_solb = figure(x_range=(xmin,xmax), plot_height=400, plot_width=950, title="Solution")
    fig_solc = figure(x_range=(xmin,xmax), plot_height=400, plot_width=950, title="Solution")
    it=0
    fig_solc.line(x, sol_init[3],line_width=2,color="Green",legend=f'sol c(x) at t={t_plot[it]:.2f}')
    fig_solb.line(x, sol_init[2],line_width=2,color="Green",legend=f'sol b(x) at t={t_plot[it]:.2f}')
    for it in range(len(sols)):
        sol=sols[it]
        fig_solc.line(x, sol[2],line_width=2,color=Category20[20][it],legend=f'sol c(x) at t={t_plot[it]:.2f}')
        fig_solb.line(x, sol[1],line_width=2,color=Category20[20][it],legend=f'sol b(x) at t={t_plot[it]:.2f}')
    fig_solb.legend.click_policy="hide" 
    fig_solc.legend.click_policy="hide"
    show(column(fig_solb,fig_solc))
if(neq==3):
    fig_sola = figure(x_range=(xmin,xmax+.5), plot_height=400, plot_width=950, title="Solution")
    fig_solb = figure(x_range=(xmin,xmax+.5), plot_height=400, plot_width=950, title="Solution")
    fig_solc = figure(x_range=(xmin,xmax+.5), plot_height=400, plot_width=950, title="Solution")
    it=0
    fig_solc.line(x, sol_init[3],line_width=2,color="Green",legend='sol c(x) at t=0.0')
    fig_solb.line(x, sol_init[2],line_width=2,color="Green",legend='sol b(x) at t=0.0')
    fig_sola.line(x, sol_init[1],line_width=2,color="Green",legend='sol a(x) at t=0.0')
    for it in range(len(sols)):
        sol=sols[it]
        #print(t_plot[it])
        fig_solc.line(x, sol[3],line_width=2,color=Category20[20][it],legend=f'sol c(x) at t={t_plot[it]}')
        fig_solb.line(x, sol[2],line_width=2,color=Category20[20][it],legend=f'sol b(x) at t={t_plot[it]}')
        fig_sola.line(x, sol[1],line_width=2,color=Category20[20][it],legend=f'sol a(x) at t={t_plot[it]}')
    fig_sola.legend.click_policy="hide"    
    fig_solb.legend.click_policy="hide" 
    fig_solc.legend.click_policy="hide" 
    show(column(fig_sola,fig_solb,fig_solc))

#  can not be converted in to a float


### Velocity

* use two point of some interval of x to get the average vitesse
* for example: $\frac{x[1]-x[0]}{time\_step}$ is the $v$ for time_step/2


In [111]:
time_step=(tend_final-tend_start)/(num_plot-1)
t_plot=np.array(t_plot)
vitesse=velocity(sols,x,time_step)
if(neq==2):
    fig_v = figure(x_range=(0,max(t_plot)),plot_height=400, plot_width=950, title="Vitesse")
    fig_v.line(t_plot-time_step/2, vitesse[1],line_width=2,color=Category20[10][1],legend=f'velocity c(t) ')
    fig_v.line(t_plot-time_step/2, vitesse[0],line_width=2,color=Category20[10][3],legend=f'velocity b(t) ')

    fig_v.x(t_plot-time_step/2, vitesse[1],line_width=2,color=Category20[10][1],legend=f'velocity c(t) ')
    fig_v.x(t_plot-time_step/2, vitesse[0],line_width=2,color=Category20[10][3],legend=f'velocity b(t) ')
    fig_v.legend.click_policy="hide"    
    fig_v.legend.location='top_left'
    show(fig_v)
if(neq==3):
    fig_v = figure(x_range=(0,max(t_plot)),plot_height=400, plot_width=950, title="Vitesse")
    fig_v.line(t_plot-time_step/2, vitesse[2],line_width=2,color=Category20[10][1],legend=f'velocity c(t) ')
    fig_v.line(t_plot-time_step/2, vitesse[1],line_width=2,color=Category20[10][3],legend=f'velocity b(t) ')
    fig_v.line(t_plot-time_step/2, vitesse[0],line_width=2,color=Category20[10][9],legend=f'velocity a(t) ')
    fig_v.x(t_plot-time_step/2, vitesse[2],line_width=2,color=Category20[10][1],legend=f'velocity c(t) ')
    fig_v.x(t_plot-time_step/2, vitesse[1],line_width=2,color=Category20[10][3],legend=f'velocity b(t) ')
    fig_v.x(t_plot-time_step/2, vitesse[0],line_width=2,color=Category20[10][9],legend=f'velocity a(t) ')
    fig_v.legend.click_policy="hide"    
    fig_v.legend.location='top_left'
    show(fig_v)

# Question2.2
### Characterize the error for several splitting time steps and plot the error as a function of splittin time step

In [9]:
#type of model (nb of equations) : 2 or 3 
neq=3
#tini: intial time
tini=0.0
#tend: final time
tend=2
#nt: nb of time discretization points to compute splitting time step
nt=int(tend*10)+1
#xmin: left limit of domain
xmin=0.0
#xmax: right limit of domain
xmax=4.0
#nx: nb of spatial discretization points
nx=4001
#method: integration method (radau5, strang)
method='strang'
#tol: tolerance for radau5 and rock4
tol='1.d-06'

neq = 3	 
tini = 0.0	 
tend = 2	 
nt = 21	 
xmin = 0.0	 
xmax = 4.0	 
nx = 4001	 
method = strang	 
tol = 1.d-06	 



### this cell is time consuming, be careful to run

In [12]:
time_steps=np.logspace(start=-1,stop=-4,num=10)
sol_ref, num_ref=read_data("sol_ref3.dat")
dx=sol_ref[0,2]-sol_ref[0,1]
int_a=np.linalg.norm(sol_ref[1])*np.sqrt(dx)
int_b=np.linalg.norm(sol_ref[2])*np.sqrt(dx)
int_c=np.linalg.norm(sol_ref[3])*np.sqrt(dx)
err_a=[]
err_b=[]
err_c=[]
for step in time_steps:
    nt=int(np.ceil(tend/step))+1
    list_input=[neq,tini,tend,nt,xmin,xmax,nx,method,tol]
    write_input(list_input)
    os.system('./bz_1d')
    sol_final,num_final=read_data("sol_num.dat")
    
    
    err_a.append(np.linalg.norm(sol_final[1]-sol_ref[1])*np.sqrt(dx))
    err_b.append(np.linalg.norm(sol_final[2]-sol_ref[2])*np.sqrt(dx))
    err_c.append(np.linalg.norm(sol_final[3]-sol_ref[3])*np.sqrt(dx))
    
err_a,err_b, err_c = err_a/int_a, err_b/int_b, err_c/int_c
tmp=np.array([err_a, err_b, err_c])
np.save('err.npy',tmp)

#  can not be converted in to a float
neq = 3	 
tini = 0.0	 
tend = 2	 
nt = 21	 
xmin = 0.0	 
xmax = 4.0	 
nx = 4001	 
method = strang	 
tol = 1.d-06	 

#  can not be converted in to a float
neq = 3	 
tini = 0.0	 
tend = 2	 
nt = 65	 
xmin = 0.0	 
xmax = 4.0	 
nx = 4001	 
method = strang	 
tol = 1.d-06	 

#  can not be converted in to a float
neq = 3	 
tini = 0.0	 
tend = 2	 
nt = 201	 
xmin = 0.0	 
xmax = 4.0	 
nx = 4001	 
method = strang	 
tol = 1.d-06	 

#  can not be converted in to a float


In [36]:
tmp=np.load('err.npy') 
err_a,err_b, err_c = tmp[0] ,tmp[1] ,tmp[2]
time_steps=np.logspace(start=-1,stop=-4,num=10)
fig_err=figure(y_range=(1.e-5,10) ,x_axis_type='log', y_axis_type='log',plot_height=400, plot_width=600, title="Strang Splitting Error(relative) - time step")
fig_err.x(time_steps,err_a, color ="Green", line_width=3, legend='relative err for a')           
fig_err.line(time_steps,err_a, color ="black", legend='relative err for a')   

fig_err.x(time_steps,err_b, color ="crimson", line_width=3,legend='relative err for b')           
fig_err.line(time_steps,err_b, color ="black", legend='relative err for b')  

fig_err.x(time_steps,err_c, color ="Blue", line_width=3, legend='relative err for c')           
fig_err.line(time_steps,err_c, color ="black", legend='relative err for c')   

fig_err.line(time_steps, time_steps**2*1.e4, color='red', line_width=2, legend='slope=2')
fig_err.legend.location="bottom_right"
show(fig_err)